# NLP Pipeline 

In [1]:
from pymongo import MongoClient
import re
import string
from sklearn.feature_extraction.text import CountVectorizer
from nltk.tokenize import TreebankWordTokenizer
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.preprocessing import Normalizer
import itertools

## Connect to the Mongo clinical_trials database 

In [2]:
def connect_to_mongo(database, collection):
    
    """
    Opens a connection to a specified Mongo DB location
    
    Input Parameters:
    database: name of database to connect to or create (str)
    collection: name of collection to connect to or create (str)
    
    Returns:
    The connection object for the database without a collection specified
    The connection object for a specific Mongo location (database & collection)
    """
    
    client = MongoClient()
    db = client[database]
    mongo_loc = db[collection]
    return db, mongo_loc

In [3]:
trials_loc, eligibility_loc = connect_to_mongo('clinical_trials', 'eligibilities')

### Create a Mongo cursor 

In [131]:
doc_cursor = eligibility_loc.find()

### Looking only at asthma 

In [176]:
asthma = eligibility_loc.find({"inclusion_criteria": { '$regex' : ".*asthma.*"}})
n = 0
for doc in asthma:
    n+=1
print(n)

2156


In [185]:
doc_cursor = eligibility_loc.find({"inclusion_criteria": { '$regex' : ".*asthma.*"}})
stemmer = PorterStemmer()
doc_count = 0

for doc in doc_cursor:
    inclusion_criteria = doc['inclusion_criteria']
    print(doc['study_id'])
    clean_criteria_list = []
    for criteria in inclusion_criteria:
        print("\nCriteria:\n -------------\n", criteria)
        remove_comma = re.sub(',', '', criteria)
        remove_equals = re.sub('/=', '', remove_comma)
        remove_period_space = re.sub('\. ', ' ', remove_equals)
        remove_less_than = re.sub('less than', '', remove_period_space)
        remove_less_than_equal = re.sub('less than or equal to', '', remove_less_than)
        remove_greater_than = re.sub('greater than', '', remove_less_than_equal)
        remove_greater_than_equal = re.sub('greater than or equal to', '', remove_greater_than)
        remove_gt_symbol = re.sub('>', '', remove_greater_than_equal)
        remove_lt_symbol = re.sub('<', '', remove_gt_symbol)
        remove_gte_symbol = re.sub('≥', '', remove_lt_symbol)
        remove_lte_symbol = re.sub('≤', '', remove_gte_symbol)
        remove_semicolon = re.sub(';', '', remove_lte_symbol)
        remove_colon = re.sub(':', '', remove_semicolon)
        remove_lparen = re.sub('\(', '', remove_colon)
        remove_rparen = re.sub('\)', '', remove_lparen)
        same_dash = re.sub('–', '-', remove_rparen)
        clean_crit = re.sub('\.$', '', same_dash)
        stem_crit = stemmer.stem(clean_crit)
        clean_criteria_list.append(stem_crit)
    print("\n Cleaned Criteria:\n-----------\n", clean_criteria_list)
    eligibility_loc.update_one({'study_id':doc['study_id']}, {"$set": {"cleaned_inclusion": clean_criteria_list}}, upsert=False)
    doc_count += 1
#     if doc_count%2000 == 0:
#         print(f'\nCleaning doc {doc_count}')
print('\nDone.')

NCT00861185

Criteria:
 -------------
 Able and willing to give written informed consent to participate in the study as HIPAA authorization;

Criteria:
 -------------
 Clinically acceptable medical history, physical examination, 12 lead ECG, vital signs, and clinical laboratory tests

Criteria:
 -------------
 History of physician-diagnosed asthma according to Global Initiative for Asthma, AND exercise-induced asthma/ bronchoconstriction;

Criteria:
 -------------
 Current treatment for asthma with short-acting inhaled beta-2-agonist ONLY;

Criteria:
 -------------
 Baseline FEV1 >65% of predicted at Screen Visit 1;

Criteria:
 -------------
 A 20% or greater drop in FEV1 following exercise challenge on at least two separate occasions prior to enrollment;

Criteria:
 -------------
 Non-smoker (refrained from any tobacco usage, or any products containing nicotine, for 6 months prior to Day 1);

 Cleaned Criteria:
-----------
 ['able and willing to give written informed consent to partic

NCT00770315

Criteria:
 -------------
 Must have a clinical history of significant ragweed-induced allergic rhinoconjunctivitis of at least 2 years duration, with or without asthma and have received treatment during the previous ragweed season (RS).

Criteria:
 -------------
 Must have a positive skin prick test response to Ambrosia artemisiifolia at Screening Visit.

Criteria:
 -------------
 Must be positive for specific immunoglobulin E (IgE) against Ambrosia artemisiifolia at Screening Visit.

Criteria:
 -------------
 Must have an forced expiratory volume in one second (FEV1) of at least 70% of predicted at Screening Visit.

Criteria:
 -------------
 Safety laboratory tests and vital signs conducted at the Screening Visit must be within normal limits or clinically acceptable to the investigator/sponsor.

Criteria:
 -------------
 Must be willing to give written informed consent and be able to adhere to dose and visit schedules.

Criteria:
 -------------
 Female participants of chi

NCT00739219

Criteria:
 -------------
 Pre-existing diagnosis of asthma

Criteria:
 -------------
 Persistent, moderate or severe asthma as classified by NAEPP

Criteria:
 -------------
 Sub-optimally controlled asthma

Criteria:
 -------------
 Initiated ICS therapy for at least the past 30 days and a history of improvement of asthma control on steroids

 Cleaned Criteria:
-----------
 ['pre-existing diagnosis of asthma', 'persistent moderate or severe asthma as classified by naepp', 'sub-optimally controlled asthma', 'initiated ics therapy for at least the past 30 days and a history of improvement of asthma control on steroid']
NCT00723021

Criteria:
 -------------
 Persistent mild/moderate asthma for at least 6 months.

Criteria:
 -------------
 Reduced lung function

Criteria:
 -------------
 Reversible airway obstruction

 Cleaned Criteria:
-----------
 ['persistent mild/moderate asthma for at least 6 month', 'reduced lung funct', 'reversible airway obstruct']
NCT00736801

Criteri

NCT00687531

Criteria:
 -------------
 Willingness to participate and comply with procedures by signing a written informed consent

Criteria:
 -------------
 12 years of age or older of either gender and any race

Criteria:
 -------------
 Women of childbearing potential (includes women who are less than 1 year postmenopausal and currently are or will become sexually active during the study) must be using or agree to use an acceptable method of birth control unless they are surgically sterilized

Criteria:
 -------------
 Must understand and be able to adhere to dosing and visit schedules, and agree to record symptom severity scores, PEFR values, medication times, and concomitant medications accurately and consistently in a daily diary.

Criteria:
 -------------
 Diagnosed history of mild-moderate persistent asthma for at least 12 months.

Criteria:
 -------------
 FEV1 must be >60% of predicted normal or personal best FEV1 during the last 12 months.

Criteria:
 -------------
 Using da

NCT00667797

Criteria:
 -------------
 Male and female subjects must be at least greater than or equal to 18 years of age at the time of consent.

Criteria:
 -------------
 Subjects must have history of asthma or COPD for at least 6 months prior to hospitalization.

Criteria:
 -------------
 Subjects must have been hospitalized due to an exacerbation of their disease and required further treatment with a nebulized beta2-adrenergic agonist.

Criteria:
 -------------
 Subjects must have an oxygen saturation level greater than or equal to 90% with greater than or equal to 40% face mask supplemental oxygen.

 Cleaned Criteria:
-----------
 ['male and female subjects must be at least  or equal to 18 years of age at the time of cons', 'subjects must have history of asthma or copd for at least 6 months prior to hospit', 'subjects must have been hospitalized due to an exacerbation of their disease and required further treatment with a nebulized beta2-adrenergic agonist', 'subjects must have an

...

NCT00930826

Criteria:
 -------------
 Clinical diagnosis of bronchial asthma

Criteria:
 -------------
 Must be able to swallow tablets

 Cleaned Criteria:
-----------
 ['clinical diagnosis of bronchial asthma', 'must be able to swallow tablet']
NCT00930163

Criteria:
 -------------
 Body weight 40 kg--150 kg

Criteria:
 -------------
 Chest radiograph with no evidence of clinically significant abnormality

Criteria:
 -------------
 Uncontrolled asthma

 Cleaned Criteria:
-----------
 ['body weight 40 kg--150 kg', 'chest radiograph with no evidence of clinically significant abnorm', 'uncontrolled asthma']
NCT00927901

Criteria:
 -------------
 Non-smoker male and female adult patients aged 18-75 years inclusive, who have signed an informed consent form prior to initiation of any study-related procedure, including any adjustments to asthma medication prior to screening.

Criteria:
 -------------
 Patients with asthma, receiving daily treatment with inhaled corticosteroid.

Criteria:
 -

NCT00914797

Criteria:
 -------------
 Physician-diagnosed asthma with positive reversibility or challenge test.

Criteria:
 -------------
 Informed consent.

Criteria:
 -------------
 Age between 18 - 45 years.

Criteria:
 -------------
 Sex: male.

Criteria:
 -------------
 Asthma classified as mild to moderate according to GINA guidelines.

Criteria:
 -------------
 Used beta-2-agonist in minimum 12 months.

 Cleaned Criteria:
-----------
 ['physician-diagnosed asthma with positive reversibility or challenge test', 'informed cons', 'age between 18 - 45 year', 'sex mal', 'asthma classified as mild to moderate according to gina guidelin', 'used beta-2-agonist in minimum 12 month']
NCT00911547

Criteria:
 -------------
 Female patients tested negative for pregnancy and agreed to use appropriate contraceptives through out the study

Criteria:
 -------------
 Patient was a nonsmoker

Criteria:
 -------------
 Patient was in good general health (except for asthma)

 Cleaned Criteria:
----

NCT00901433

Criteria:
 -------------
 Male/female age 18 years and up.

Criteria:
 -------------
 Subject is diagnosed as an asthmatic, or subject is parent/guardian of an asthmatic child age under 18 years.

Criteria:
 -------------
 Subject understands the study procedure.

Criteria:
 -------------
 Subject is able to read the User Manual.

Criteria:
 -------------
 Signed Informed Consent form

Criteria:
 -------------
 Compliance with study requirements.

 Cleaned Criteria:
-----------
 ['male/female age 18 years and up', 'subject is diagnosed as an asthmatic or subject is parent/guardian of an asthmatic child age under 18 year', 'subject understands the study procedur', 'subject is able to read the user manu', 'signed informed consent form', 'compliance with study requir']
NCT00900874

Criteria:
 -------------
 clinical asthma score (or pulmonary index score-annexure 1) between 6-9

 Cleaned Criteria:
-----------
 ['clinical asthma score or pulmonary index score-annexure 1 betwee

NCT00873873

Criteria:
 -------------
 Must be enrolled in the CAMPCS/3 study; individuals enrolled in this study will represent four different patterns of asthma progression, as defined by forced expiratory volume in 1 second (FEV1)/forced vital capacity (FVC) levels

 Cleaned Criteria:
-----------
 ['must be enrolled in the campcs/3 study individuals enrolled in this study will represent four different patterns of asthma progression as defined by forced expiratory volume in 1 second fev1/forced vital capacity fvc level']
NCT00873860

Criteria:
 -------------
 Male or female subjects

Criteria:
 -------------
 Age 18 to 65 years at the time of Screening

Criteria:
 -------------
 Subjects must have a body mass index (BMI) between 18 and 40 kilogram per square meter (kg/m^2)

Criteria:
 -------------
 Written informed consent obtained from the subject prior to performing any protocol related procedures, including Screening evaluations

Criteria:
 -------------
 Physician-diagnosed mode

NCT00867906

Criteria:
 -------------
 Male or female, aged 18-65 years.

Criteria:
 -------------
 A history of controlled asthma as defined in GINA (2007) on exposure to cats for at least 1 year

Criteria:
 -------------
 Asthma controlled with:Inhaled salbutamol (Cohort 1), Inhaled corticosteroid (Cohort 2), Inhaled corticosteroid plus a long acting β2agonist (LABA) (Cohort 3) Treatment for asthma must have been stable (drug(s), dose, frequency) for at least 3 months.

Criteria:
 -------------
 A reliable history of rhinoconjunctivitis (sneezing, rhinorrhoea, nasal blockage, itchy/red/sore/watering eyes) on exposure to cats for at least 1 year.

Criteria:
 -------------
 Subjects who provide written informed consent.

Criteria:
 -------------
 Positive skin prick test to cat allergen with a wheal diameter at least 3mm larger than that produced by the negative control.

Criteria:
 -------------
 A LPSR to cat allergen eight hours after intradermal injection of greater than 25mm diame

In [186]:
doc_cursor = eligibility_loc.find({"inclusion_criteria": { '$regex' : ".*asthma.*"}})
stemmer = PorterStemmer()
doc_count = 0

for doc in doc_cursor:
    exclusion_criteria = doc['exclusion_criteria']
    print(doc['study_id'])
    clean_criteria_list = []
    for criteria in exclusion_criteria:
        print("\nCriteria:\n -------------\n", criteria)
        remove_comma = re.sub(',', '', criteria)
        remove_equals = re.sub('/=', '', remove_comma)
        remove_period_space = re.sub('\. ', ' ', remove_equals)
        remove_less_than = re.sub('less than', '', remove_period_space)
        remove_less_than_equal = re.sub('less than or equal to', '', remove_less_than)
        remove_greater_than = re.sub('greater than', '', remove_less_than_equal)
        remove_greater_than_equal = re.sub('greater than or equal to', '', remove_greater_than)
        remove_gt_symbol = re.sub('>', '', remove_greater_than_equal)
        remove_lt_symbol = re.sub('<', '', remove_gt_symbol)
        remove_gte_symbol = re.sub('≥', '', remove_lt_symbol)
        remove_lte_symbol = re.sub('≤', '', remove_gte_symbol)
        remove_semicolon = re.sub(';', '', remove_lte_symbol)
        remove_colon = re.sub(':', '', remove_semicolon)
        remove_lparen = re.sub('\(', '', remove_colon)
        remove_rparen = re.sub('\)', '', remove_lparen)
        same_dash = re.sub('–', '-', remove_rparen)
        clean_crit = re.sub('\.$', '', same_dash)
        stem_crit = stemmer.stem(clean_crit)
        clean_criteria_list.append(stem_crit)
    print("\n Cleaned Criteria:\n-----------\n", clean_criteria_list)
    eligibility_loc.update_one({'study_id':doc['study_id']}, {"$set": {"cleaned_exclusion": clean_criteria_list}}, upsert=False)
    doc_count += 1
#     if doc_count%2000 == 0:
#         print(f'\nCleaning doc {doc_count}')
print('\nDone.')

NCT00861185

Criteria:
 -------------
 Subject who has experienced any allergic reaction to a drug which, suggests an increased potential for a hypersensitivity to senicapoc (e.g., clotrimazole);

Criteria:
 -------------
 Previous ingestion of senicapoc (ICA-17043)

Criteria:
 -------------
 Pregnant or lactating female;

Criteria:
 -------------
 Condition that might interfere with the absorption, distribution, metabolism, and/or excretion of drugs; subjects who have had any previous gastrointestinal surgery, except appendectomy or cholecystectomy (if performed more than 90 days prior to Screening Visit 1) or a history of clinically significant active cardiovascular, neurologic, endocrine, hepatic, or renal disorders;

Criteria:
 -------------
 Infectious illness, e.g. acute bacterial, acute and chronic parasitic, fungal infection or viral infection within 6 weeks prior to Screening Visit 1 or between Screening Visit 1 and Day 1 (Randomization).

Criteria:
 -------------
 Treatment f

NCT00800241

Criteria:
 -------------
 currently participating or have participated in a study with an investigational compound within the last 30 days

Criteria:
 -------------
 current diagnosis of chronic obstructive pulmonary disease (COPD)

 Cleaned Criteria:
-----------
 ['currently participating or have participated in a study with an investigational compound within the last 30 day', 'current diagnosis of chronic obstructive pulmonary disease copd']
NCT00788749

Criteria:
 -------------
 unilateral nasal polyposis

Criteria:
 -------------
 polypoid lesion suspicious of inverted papilloma, malignancy, Wegeners granulomatosis, sarcoidosis

Criteria:
 -------------
 known or suspected hypersensitivity to fluticasone propionate or any other constituents of the Investigational Medicinal product (IMP).

Criteria:
 -------------
 Any clinically significant medical condition or abnormality, which, in the opinion of the investigator, might compromise the safety of the subject or which m

NCT00739219

Criteria:
 -------------
 Active cigarette smoking or ≥ 10 pack-years smoking history

Criteria:
 -------------
 Xolair taken in the past 6 months prior to enrollment

Criteria:
 -------------
 Oral prednisone taken in the last 4 weeks prior to enrollment

Criteria:
 -------------
 Cystic Fibrosis, COPD, ciliary dyskinesia, chest wall deformities or scoliosis

 Cleaned Criteria:
-----------
 ['active cigarette smoking or  10 pack-years smoking histori', 'xolair taken in the past 6 months prior to enrol', 'oral prednisone taken in the last 4 weeks prior to enrol', 'cystic fibrosis copd ciliary dyskinesia chest wall deformities or scoliosi']
NCT00723021

Criteria:
 -------------
 Pregnant/nursing females.

 Cleaned Criteria:
-----------
 ['pregnant/nursing femal']
NCT00736801

Criteria:
 -------------
 No regular treatment (only short-acting inhalers on demand were allowed)

Criteria:
 -------------
 No history of or evidence for any other chronic disease than asthma

 Clean

NCT00689806

Criteria:
 -------------
 Pregnancy or lactation

Criteria:
 -------------
 Severe metabolic disease

Criteria:
 -------------
 Other respiratory or inflammatory disorders (sarcoidosis, emphysema)

Criteria:
 -------------
 Hypokalemia, dehydration

Criteria:
 -------------
 Uncontrolled seizure disorder ( 2 or more seizures in last year)

Criteria:
 -------------
 Major surgery, trauma

Criteria:
 -------------
 Pre-existing liver disease (AST or ALT >10% above the upper limit of normal)

Criteria:
 -------------
 Elevated CK (>50% above the upper limit of normal)

Criteria:
 -------------
 History of alcohol abuse

Criteria:
 -------------
 Current smokers or ex-smokers with > 10 pack-years of smoking

Criteria:
 -------------
 Partial ileal bypass surgery

Criteria:
 -------------
 Concurrent treatment with drugs known to be have potential interactions or associated with rhabdomyolysis (Cimetadine, danazole, delavaridine, diltiazem, fenofiibrate, nefazodone, niacin, pro

NCT00670930

Criteria:
 -------------
 Patients who've had an asthma exacerbation during the 4 weeks prior to randomization

Criteria:
 -------------
 Current smokers, stopped smoking within the last 12 months or have a smoking history of >10 pack years

Criteria:
 -------------
 History of severe allergy to food or drugs

Criteria:
 -------------
 Previous treatment with omalizumab

Criteria:
 -------------
 Any patient considered to be unsuitable to bronchoscopy, according to the judgment of the investigator

 Cleaned Criteria:
-----------
 ["patients who've had an asthma exacerbation during the 4 weeks prior to random", 'current smokers stopped smoking within the last 12 months or have a smoking history of 10 pack year', 'history of severe allergy to food or drug', 'previous treatment with omalizumab', 'any patient considered to be unsuitable to bronchoscopy according to the judgment of the investig']
NCT00667992

Criteria:
 -------------
 Known or suspected hypersensitivity to bude

...

NCT00918944

 Cleaned Criteria:
-----------
 []
NCT00917410

Criteria:
 -------------
 below 18 and above 45

Criteria:
 -------------
 COPD patients

Criteria:
 -------------
 no mobile phone

 Cleaned Criteria:
-----------
 ['below 18 and above 45', 'copd pati', 'no mobile phon']
NCT00917215

Criteria:
 -------------
 acupuncture for asthma within 12 months of the study

Criteria:
 -------------
 emergency department visit within one month of the study

Criteria:
 -------------
 hospitalization for asthma within three months of the study

Criteria:
 -------------
 severe upper respiratory tract infections within six weeks of the study

Criteria:
 -------------
 systemic infections, cancers, autoimmune disorders, cardiac failures, myofacial infarcts,angina pectoris, renal failures or hepato-biliary diseases

 Cleaned Criteria:
-----------
 ['acupuncture for asthma within 12 months of the studi', 'emergency department visit within one month of the studi', 'hospitalization for asthma wi

NCT00910585

 Cleaned Criteria:
-----------
 []
NCT00909779

Criteria:
 -------------
 Female subjects who are pregnant or lactating.

Criteria:
 -------------
 Subjects with a history of asthma, with the exception of asthma diagnosed in childhood.

Criteria:
 -------------
 Subjects with a blood eosinophil count >5% of total white blood cell count.

Criteria:
 -------------
 Subjects with a febrile illness within 3 days before Screening.

Criteria:
 -------------
 Subjects with a malignant neoplasm other than non melanomatous basal cell skin cancer. Subjects with a history of malignancy who have been cancer free for 5 years or more may be enrolled.

Criteria:
 -------------
 Subjects who are currently using disallowed medications or will be unable to complete the medication washout periods. Subjects taking a prohibited concurrent medication which requires a washout of >30 days may be rescreened when the washout of the prohibited concurrent medication has been met.

Criteria:
 --------

NCT00892684

Criteria:
 -------------
 Soy allergy

Criteria:
 -------------
 Fish allergy

Criteria:
 -------------
 Treatment with anti-coagulation

 Cleaned Criteria:
-----------
 ['soy allergi', 'fish allergi', 'treatment with anti-coagul']
NCT00890877

 Cleaned Criteria:
-----------
 []
NCT00890734

Criteria:
 -------------
 Use of oral corticosteroids within past 3 months

Criteria:
 -------------
 Hospitalization for asthma exacerbation within past 6 months

Criteria:
 -------------
 Uncontrolled asthma

Criteria:
 -------------
 Contraindication to any study test or procedure

 Cleaned Criteria:
-----------
 ['use of oral corticosteroids within past 3 month', 'hospitalization for asthma exacerbation within past 6 month', 'uncontrolled asthma', 'contraindication to any study test or procedur']
NCT00890539

Criteria:
 -------------
 You have a known hypersensitivity (i.e. an overreaction of your immune system) to methacholine or other parasympathomimetic agents or cholinesterase 

NCT00868023

Criteria:
 -------------
 Pregnant or lactating women or all women physiologically capable of becoming pregnant UNLESS they are menopausal or are using effective and acceptable methods of contraception.

Criteria:
 -------------
 Significant seasonal variation in asthma or asthma occurring only during episodic exposure to an allergen or a chemical sensitizer.

Criteria:
 -------------
 History of near fatal asthma (e.g. brittle asthma, hospitalisation for asthma exacerbation in Intensive Care Unit) within 1 year before screening.

Criteria:
 -------------
 Occurrence of asthma exacerbations or respiratory tract infections in the 4 weeks preceding the screening visit.

Criteria:
 -------------
 Diagnosis of Chronic Obstructive Pulmonary Disease (COPD)

Criteria:
 -------------
 History of cystic fibrosis, bronchiectasis or alpha-1 antitrypsin deficiency.

Criteria:
 -------------
 Diagnosis of restrictive lung disease.

Criteria:
 -------------
 Patients treated with oral o

NCT00867737

Criteria:
 -------------
 Severe asthma

 Cleaned Criteria:
-----------
 ['severe asthma']

Done.


In [ ]:
doc_cursor = eligibility_loc.find({"inclusion_criteria": { '$regex' : ".*asthma.*"}})

## Clean the text 

### Test on 5 entires 

In [6]:
doc_cursor = eligibility_loc.find().limit(5)
stemmer = PorterStemmer()

for doc in doc_cursor:
    inclusion_criteria = doc['inclusion_criteria']
    print(doc['study_id'])
    clean_criteria_list = []
    for criteria in inclusion_criteria:
        print("\nCriteria:\n -------------\n", criteria)
        remove_comma = re.sub(',', '', criteria)
        remove_equals = re.sub('/=', '', remove_comma)
        remove_period_space = re.sub('\. ', ' ', remove_equals)
        remove_less_than = re.sub('less than', '', remove_period_space)
        remove_less_than_equal = re.sub('less than or equal to', '', remove_less_than)
        remove_greater_than = re.sub('greater than', '', remove_less_than_equal)
        remove_greater_than_equal = re.sub('greater than or equal to', '', remove_greater_than)
        remove_gt_symbol = re.sub('>', '', remove_greater_than_equal)
        remove_lt_symbol = re.sub('<', '', remove_gt_symbol)
        remove_gte_symbol = re.sub('≥', '', remove_lt_symbol)
        remove_lte_symbol = re.sub('≤', '', remove_gte_symbol)
        remove_semicolon = re.sub(';', '', remove_lte_symbol)
        remove_colon = re.sub(':', '', remove_semicolon)
        remove_lparen = re.sub('\(', '', remove_colon)
        remove_rparen = re.sub('\)', '', remove_lparen)
        same_dash = re.sub('–', '-', remove_rparen)
        clean_crit = re.sub('\.$', '', same_dash)
        stem_crit = stemmer.stem(clean_crit)
        clean_criteria_list.append(stem_crit)
    print("\n Cleaned Criteria:\n-----------\n", clean_criteria_list)
    eligibility_loc.update_one({'study_id':doc['study_id']}, {"$set": {"cleaned_inclusion": clean_criteria_list}}, upsert=False)
    doc_count += 1
#     if doc_count%2000 == 0:
#         print(f'\nCleaning doc {doc_count}')
print('\nDone.')

NCT00864942

Criteria:
 -------------
 Documented relapsed or refractory B-cell NHL; CD-20 positive tumor. Indolent NHL: follicular B-cell lymphoma, diffuse small lymphocytic lymphoma, lymphoplasmacytic lymphoma, marginal zone lymphoma, transformed aggressive lymphomas, mantle cell lymphoma and chronic lymphocytic leukemia

Criteria:
 -------------
 Maximum of 6 prior chemotherapy regimens. Prior rituximab is allowed.

Criteria:
 -------------
 Bidimensionally measurable disease

Criteria:
 -------------
 ECOG performance status 0-2

Criteria:
 -------------
 Absolute neutrophil count >/= 1000 and platelet count >/= 50,000

Criteria:
 -------------
 Serum creatinine </= 1.5 mg/dL

Criteria:
 -------------
 Adequate hepatic function

Criteria:
 -------------
 Estimated life expectancy of at least 3 months

Criteria:
 -------------
 All study participants must be registered into the mandatory RevAssist program and be willing and able to comply with the requirements of RevAssist

Criteria

### Clean inclusion criteria for all documents 

In [7]:
doc_cursor = eligibility_loc.find()
stemmer = PorterStemmer()

for doc in doc_cursor:
    inclusion_criteria = doc['inclusion_criteria']
#     print(doc['study_id'])
    clean_criteria_list = []
    for criteria in inclusion_criteria:
#         print("\nCriteria:\n -------------\n", criteria)
        remove_comma = re.sub(',', '', criteria)
        remove_equals = re.sub('/=', '', remove_comma)
        remove_period_space = re.sub('\. ', ' ', remove_equals)
        remove_less_than = re.sub('less than', '', remove_period_space)
        remove_less_than_equal = re.sub('less than or equal to', '', remove_less_than)
        remove_greater_than = re.sub('greater than', '', remove_less_than_equal)
        remove_greater_than_equal = re.sub('greater than or equal to', '', remove_greater_than)
        remove_gt_symbol = re.sub('>', '', remove_greater_than_equal)
        remove_lt_symbol = re.sub('<', '', remove_gt_symbol)
        remove_gte_symbol = re.sub('≥', '', remove_lt_symbol)
        remove_lte_symbol = re.sub('≤', '', remove_gte_symbol)
        remove_semicolon = re.sub(';', '', remove_lte_symbol)
        remove_colon = re.sub(':', '', remove_semicolon)
        remove_lparen = re.sub('\(', '', remove_colon)
        remove_rparen = re.sub('\)', '', remove_lparen)
        same_dash = re.sub('–', '-', remove_rparen)
        clean_crit = re.sub('\.$', '', same_dash)
        stem_crit = stemmer.stem(clean_crit)
        clean_criteria_list.append(stem_crit)
#     print("\n Cleaned Criteria:\n-----------\n", clean_criteria_list)
    eligibility_loc.update_one({'study_id':doc['study_id']}, {"$set": {"cleaned_inclusion": clean_criteria_list}}, upsert=False)
    doc_count += 1
    if doc_count%2000 == 0:
        print(f'\nCleaning doc {doc_count}')
print('\nDone.')


Cleaning doc 2000

Cleaning doc 4000

Cleaning doc 6000

Cleaning doc 8000

Cleaning doc 10000

Cleaning doc 12000

Cleaning doc 14000

Cleaning doc 16000

Cleaning doc 18000

Cleaning doc 20000

Cleaning doc 22000

Cleaning doc 24000

Cleaning doc 26000

Cleaning doc 28000

Cleaning doc 30000

Cleaning doc 32000

Cleaning doc 34000

Cleaning doc 36000

Cleaning doc 38000

Cleaning doc 40000

Cleaning doc 42000

Cleaning doc 44000

Cleaning doc 46000

Cleaning doc 48000

Cleaning doc 50000

Cleaning doc 52000

Cleaning doc 54000

Cleaning doc 56000

Cleaning doc 58000

Cleaning doc 60000

Cleaning doc 62000

Cleaning doc 64000

Cleaning doc 66000

Cleaning doc 68000

Cleaning doc 70000

Cleaning doc 72000

Cleaning doc 74000

Cleaning doc 76000

Cleaning doc 78000

Cleaning doc 80000

Cleaning doc 82000

Cleaning doc 84000

Cleaning doc 86000

Cleaning doc 88000

Cleaning doc 90000

Cleaning doc 92000

Cleaning doc 94000

Cleaning doc 96000

Cleaning doc 98000

Cleaning doc 100000


CursorNotFound: cursor id 314779460464 not found

## Vectorize 

### Unpack inclusion critera so we can fit each one to the vectorizer separately 

In [227]:
single_doc = [['crit1', 'crit2', 'crit3'], ['crita', 'critb']]
list(itertools.chain(*single_doc))
# use mongo explode next time

['crit1', 'crit2', 'crit3', 'cirta', 'critb']

### Test that unpacking works with the cursor to create a list the vectorizer will accept

In [234]:
trials_loc, eligibility_loc = connect_to_mongo('clinical_trials', 'eligibilities')
doc_cursor = eligibility_loc.find().limit(2)

unpacked_criteria = list(itertools.chain(*(doc['cleaned_inclusion'] for doc in doc_cursor)))
unpacked_criteria

['documented relapsed or refractory b-cell nhl cd-20 positive tumor indolent nhl follicular b-cell lymphoma diffuse small lymphocytic lymphoma lymphoplasmacytic lymphoma marginal zone lymphoma transformed aggressive lymphomas mantle cell lymphoma and chronic lymphocytic leukemia',
 'maximum of 6 prior chemotherapy regimens prior rituximab is allow',
 'bidimensionally measurable diseas',
 'ecog performance status 0-2',
 'absolute neutrophil count > 1000 and platelet count > 50000',
 'serum creatinine < 1.5 mg/dl',
 'adequate hepatic funct',
 'estimated life expectancy of at least 3 month',
 'all study participants must be registered into the mandatory revassist program and be willing and able to comply with the requirements of revassist',
 'able to take aspirin 81 mg daily as prophylactic anticoagul',
 'patient was diagnosed as nosocomial infection defined according to criteria established by the us cdc the diagnosis criteria for ventilator-associated pneumonia are modified from those e

### Create vectorizer 

In [25]:
cv = CountVectorizer(ngram_range=(1, 3),
                                   analyzer='word',
                                   stop_words='english', 
                                   token_pattern="[a-z][a-z]+",
                                   lowercase=True,
                                   max_df = 0.4,
                                   min_df = 2)

### Fit vectorizer on 100000 docs

In [17]:
trials_loc, eligibility_loc = connect_to_mongo('clinical_trials', 'eligibilities')
doc_cursor = eligibility_loc.find().limit(100000)

X = count_vectorizer.fit(list(itertools.chain(*(doc['cleaned_inclusion'] for doc in doc_cursor))))

In [19]:
X.get_feature_names()

['aa anaplastic',
 'aa anaplastic oligodendroglioma',
 'aa ao',
 'aa ao aoa',
 'aa confirmed',
 'aa criteria',
 'aa diagnostic',
 'aa diagnostic criteria',
 'aa metabolism',
 'aa metabolism ex',
 'aa treat',
 'aa treatment',
 'aa treatment advanced',
 'aa treatment received',
 'aa tumor',
 'aa working',
 'aa working group',
 'aaa angle',
 'aaa cm',
 'aaa cm diameter',
 'aaa diameter',
 'aaa diameter cm',
 'aaa equal',
 'aaa equal cm',
 'aaa growth',
 'aaa growth mm',
 'aaa iliac',
 'aaa iliac artery',
 'aaa increased',
 'aaa increased equal',
 'aaa maximum',
 'aaa maximum diameter',
 'aaa maximum external',
 'aaa mm',
 'aaa mm length',
 'aaa neck',
 'aaa neck distance',
 'aaa proximal',
 'aaa proximal neck',
 'aaa repair',
 'aabb standards',
 'aabb standards note',
 'aad equipped',
 'aad paf',
 'aad paf class',
 'aad therapy',
 'aadc inhibitor',
 'aalborg included',
 'aalborg included studi',
 'aalborg university',
 'aalborg university hospit',
 'aall eligibility',
 'aall eligibility p

### Transform 100000 docs

In [20]:
trials_loc, eligibility_loc = connect_to_mongo('clinical_trials', 'eligibilities')
doc_cursor = eligibility_loc.find().limit(100000)

X_trans = count_vectorizer.transform(' '.join(doc['cleaned_inclusion']) for doc in doc_cursor)

In [24]:
X_trans

0

In [256]:
X_array = X.toarray()

In [260]:
X_array

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ..., 
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

## Vectorize, transform, partial fit for lda

### Fit model to 1k transformed dataset 

In [43]:
from nltk.corpus import stopwords


In [138]:
stop = stopwords.words('english')
remove = ['consent', 'informed', 'written', 'sign', 'year', 'age', 'access', 'relevant', 'reliable', 'medical', 'ability', 'suggest', 'undergo', 'acceptable', 'understand', 'purposes', 'managed', 'ability', 'study', 'abnormalities', 'abnormality', 'kg', 'mg', 'weight', 'subject', 'years', 'months', 'least', 'able', 'screening', 'diagnosis', 'patient', 'day', 'per', 'level', 'required', 'non', 'may', 'subjects', 'days', 'prior', 'iii', 'iv', 'willing', 'comply', 'must', 'patients', 'within', 'last', 'agree', 'use', 'criteria', 'defined', 'taking', 'enrollment', 'enrolled', 'hours', 'first', 'month', 'group', 'present', 'ii', 'duration', 'read', 'adequate', 'normal', 'entry', 'meet', 'week', 'approved', 'etc', 'likely', 'would', 'regular']
stop+= remove
print(stop)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [165]:
cv = CountVectorizer(ngram_range=(1,1),
                                   analyzer='word',
                                   stop_words=stop, 
                                   token_pattern="[a-z][a-z]+",
                                   lowercase=True,
                                   max_df = 0.6,
                                   min_df = 2)

In [166]:
n_components = 50
n_iter = 10
lda = LatentDirichletAllocation(n_components=n_components,
                                max_iter=n_iter,
                                random_state=42,
                               learning_method='online')


trials_loc, eligibility_loc = connect_to_mongo('clinical_trials', 'eligibilities')
doc_cursor = eligibility_loc.find().limit(5000)

cv.fit(list(itertools.chain(*(doc['cleaned_inclusion'] for doc in doc_cursor))))

trials_loc, eligibility_loc = connect_to_mongo('clinical_trials', 'eligibilities')
doc_cursor = eligibility_loc.find().limit(5000)

post_gen = (' '.join(doc['cleaned_inclusion']) for doc in doc_cursor)
for doc in post_gen:
    vec_doc = cv.transform([doc])
    lda.partial_fit(vec_doc)

In [167]:
def display_topics(model, feature_names, no_top_words):
    for ix, topic in enumerate(model.components_):
        print("Topic ", ix)
        print(", ".join([feature_names[i]
                        for i in topic.argsort()[:-no_top_words - 1:-1]]))
        
display_topics(lda,cv.get_feature_names(),20)

Topic  0
presence, central, guidelines, idiopathic, elevation, demonstrated, retinal, focal, serous, optical, visual, pancreat, acuity, secondary, thickness, vegf, choroidal, amd, subfoveal, cnv
Topic  1
history, clinical, laboratory, body, clinically, bmi, index, mass, physical, inclus, available, examination, exercise, ecg, lower, lead, abov, full, detailed, approximately
Topic  2
target, achieved, characteristics, mm, stent, coronary, endeavor, sonovue, ce, single, visually, vessel, planned, anticoagulation, case, antagonist, performed, artery, length, requir
Topic  3
childbearing, active, pregnant, agents, sexually, doses, lactating, feeding, randomization, neither, low, hcg, specific, following, hormonal, vasectomized, oth, return, visit, voluntarily
Topic  4
drug, medication, range, general, volunteers, initiation, histori, limited, pounds, selected, gastrointestinal, sitting, electrocardiogram, shall, observations, potential, volunteer, time, evaluation, include
Topic  5
regular

In [41]:
for doc in eligibility_loc.find()[:5]:
    vec_doc = cv.transform([' '.join(doc['cleaned_inclusion'])])
    new_vec = lda.transform(vec_doc)
    print(new_vec)

[[ 0.00185188  0.00185185  0.00185186  0.00185186  0.27484228  0.00185186
   0.00185189  0.00185187  0.71034278  0.00185186]]
[[ 0.01111111  0.01111111  0.01111111  0.01111148  0.01111127  0.12223102
   0.01111211  0.67776521  0.01111112  0.12222445]]
[[ 0.00588385  0.00588301  0.00588246  0.00588346  0.00588437  0.61275878
   0.00588282  0.00588246  0.00588282  0.34017597]]
[[ 0.1  0.1  0.1  0.1  0.1  0.1  0.1  0.1  0.1  0.1]]
[[ 0.00588241  0.00588235  0.00588238  0.82939572  0.00588267  0.06400763
   0.00588238  0.00588237  0.06541958  0.00588251]]


# Next steps 

## Improving the pipeline 

* Refactor `connect_to_mongo()` function so we don't have to reconnect when switching databases (might be able to pull this into other functions later on)
* Scrutinize stopwords - currently using default, there may be some words worth including such as 'not'

## Error checking and production aspects to add   

* Error messages
* docstrings
* create functions
* comments to explain hard-coding choices or why an approach was used
* Add test cases for cleaning